<a href="https://colab.research.google.com/github/rayou2/AutoML-examples/blob/main/AutoML.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Install Packages

In [ ]:
!pip install tpot mljar-supervised

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 87 kB 3.1 MB/s 
     |████████████████████████████████| 112 kB 30.5 MB/s 
     |████████████████████████████████| 139 kB 34.4 MB/s 
     |████████████████████████████████| 255.9 MB 43 kB/s 
     |████████████████████████████████| 2.0 MB 42.3 MB/s 
     |████████████████████████████████| 76.6 MB 1.2 MB/s 
     |████████████████████████████████| 72 kB 855 kB/s 
     |████████████████████████████████| 569 kB 45.0 MB/s 
     |████████████████████████████████| 72 kB 819 kB/s 
     |████████████████████████████████| 348 kB 67.6 MB/s 
     |████████████████████████████████| 209 kB 45.5 MB/s 
     |████████████████████████████████| 81 kB 9.0 MB/s 
     |████████████████████████████████| 78 kB 7.1 MB/s 
     |████████████████████████████████| 147 kB 49.4 MB/s 
     |████████████████████████████████| 112 kB 54.9 MB/s 
     |████████████████████████████████| 5

In [ ]:
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split
from supervised.automl import AutoML

# Options Available

*  mode — the package ships with four built-in models.
      *  The Explain mode is ideal for explaining and understanding the data. It results in visualizations of feature importance as well as tree visualizations.
      *  The Perform is used when building ML models for production.
      *  The Compete is meant to build models used in machine learning competitions.
      *  The Optuna mode is used to search for highly-tuned ML models.
*  algorithms — specifies the algorithms you would like to use. They are usually passed in as a list.
*  results_path — the path where the results will be stored
*  total_time_limit — the total time in seconds for training the model
*  train_ensemble — dictates if an ensemble will be created at the end of the training process
*  stack_models — determines if a models stack will be created
*  eval_metric — the metric that will be optimized. If auto the logloss is used for classification problems while the rmse is used for regression problems

In [ ]:
#automl = AutoML(
    # mode="Explain"
    # algorithms=""
    # results_path="AutoML_22",
    # total_time_limit= 30 * 60,
    # train_ensemble=true,
    # stack_models="",
    # eval_metric=""
#)

# Healthcare Dataset - SPARCS

## Load in dataset

In [ ]:
import pandas as pd
tuition = pd.read_csv('/content/Tuition_Assistance_Program__TAP__Recipients___Dollars_by_College__Sector_Group__and_Level_of_Study__Beginning_2000.csv')
tuition

Academic Year  TAP College Code  Federal School Code Level  \
0               2020              1075                 7465     U   
1               2020              8323                42785     U   
2               2020              1040                 2899     U   
3               2020              8244                 7264     U   
4               2020              1016                 2894     U   
...              ...               ...                  ...   ...   
11121           2000              5215                 2688     G   
11122           2000               535                20662     U   
11123           2000               965                 7109     U   
11124           2000              5210                 2681     G   
11125           2000              5205                 2687     G   

      TAP Level of Study                  TAP College Name Sector Type  \
0         2 yr Undergrad    AMERICAN ACAD OF DRAMATIC ARTS     PRIVATE   
1         4 yr Undergrad            YESHIVA HECHAL SHEMUEL     PRIVATE   
2         4 yr Undergrad      WAGNER COLLEGE 4YR UNDERGRAD     PRIVATE   
3         4 yr Undergrad  MESIVTA TORAH VODAATH RABBINICAL     PRIVATE   
4         4 yr Undergrad      UNIV OF ROCHESTER EASTMAN UG     PRIVATE   
...                  ...                               ...         ...   
11121               Grad            CUNY CITY COLLEGE GRAD      PUBLIC   
11122     5 yr Undergrad      THE NEW SCHOOL 4YR UNDERGRAD     PRIVATE   
11123     2 yr Undergrad      SUC OLD WESTBURY (UNDERGRAD)      PUBLIC   
11124               Grad             CANISIUS COLLEGE GRAD     PRIVATE   
11125               Grad        CUNY BROOKLYN COLLEGE GRAD      PUBLIC   

      TAP Sector Group  TAP Recipient Headcount  TAP Recipient FTEs  \
0        5-INDEPENDENT                        3                3.06   
1       9-CHAPTER XXII                        7                7.03   
2        5-INDEPENDENT                      252              239.09   
3       9-CHAPTER XXII                      127              130.41   
4        5-INDEPENDENT                       14               12.73   
...                ...                      ...                 ...   
11121        1-CUNY SR                       56               41.75   
11122    5-INDEPENDENT                       22               12.25   
11123        3-SUNY SO                       10                6.75   
11124    5-INDEPENDENT                       44               31.75   
11125        1-CUNY SR                       66               44.25   

       TAP Recipient Dollars  
0                   12364.30  
1                   25198.17  
2                  722802.93  
3                  551196.83  
4                   30044.02  
...                      ...  
11121               17967.00  
11122               41006.00  
11123               18912.25  
11124               10030.75  
11125               18172.50  

[11126 rows x 11 columns]

In [ ]:
tuition.columns

Index(['Academic Year', 'TAP College Code', 'Federal School Code', 'Level',
       'TAP Level of Study', 'TAP College Name', 'Sector Type',
       'TAP Sector Group', 'TAP Recipient Headcount', 'TAP Recipient FTEs',
       'TAP Recipient Dollars'],
      dtype='object')

## Potential variables of interest

* TAP Level of Study (categorical) 
* TAP Recipient Dollars (continuous)
* Level




In [ ]:
tuition['TAP Level of Study'].describe()

count              11126
unique                 6
top       4 yr Undergrad
freq                3945
Name: TAP Level of Study, dtype: object

In [ ]:
tuition['TAP Level of Study'].value_counts()

4 yr Undergrad    3945
2 yr Undergrad    3286
5 yr Undergrad    2367
Grad              1487
STAP                39
Unknown              2
Name: TAP Level of Study, dtype: int64

In [ ]:
tuition['TAP Recipient Dollars'].describe()

count    1.112600e+04
mean     1.599339e+06
std      3.303060e+06
min      1.875000e+01
25%      1.795453e+04
50%      1.538812e+05
75%      1.662690e+06
max      3.393526e+07
Name: TAP Recipient Dollars, dtype: float64

In [ ]:
tuition['Level'].value_counts()

U    9633
G    1493
Name: Level, dtype: int64

# Create new model

In [ ]:
x = tuition.drop(columns =['TAP Level of Study'])

In [ ]:
y = tuition["TAP Level of Study"]

In [ ]:
x

Academic Year  TAP College Code  Federal School Code  \
0               2020              1075                 7465   
1               2020              8323                42785   
2               2020              1040                 2899   
3               2020              8244                 7264   
4               2020              1016                 2894   
...              ...               ...                  ...   
11121           2000              5215                 2688   
11122           2000               535                20662   
11123           2000               965                 7109   
11124           2000              5210                 2681   
11125           2000              5205                 2687   

                       TAP College Name Sector Type TAP Sector Group  \
0        AMERICAN ACAD OF DRAMATIC ARTS     PRIVATE    5-INDEPENDENT   
1                YESHIVA HECHAL SHEMUEL     PRIVATE   9-CHAPTER XXII   
2          WAGNER COLLEGE 4YR UNDERGRAD     PRIVATE    5-INDEPENDENT   
3      MESIVTA TORAH VODAATH RABBINICAL     PRIVATE   9-CHAPTER XXII   
4          UNIV OF ROCHESTER EASTMAN UG     PRIVATE    5-INDEPENDENT   
...                                 ...         ...              ...   
11121            CUNY CITY COLLEGE GRAD      PUBLIC        1-CUNY SR   
11122      THE NEW SCHOOL 4YR UNDERGRAD     PRIVATE    5-INDEPENDENT   
11123      SUC OLD WESTBURY (UNDERGRAD)      PUBLIC        3-SUNY SO   
11124             CANISIUS COLLEGE GRAD     PRIVATE    5-INDEPENDENT   
11125        CUNY BROOKLYN COLLEGE GRAD      PUBLIC        1-CUNY SR   

       TAP Recipient Headcount  TAP Recipient FTEs  TAP Recipient Dollars  \
0                            3                3.06               12364.30   
1                            7                7.03               25198.17   
2                          252              239.09              722802.93   
3                          127              130.41              551196.83   
4                           14               12.73               30044.02   
...                        ...                 ...                    ...   
11121                       56               41.75               17967.00   
11122                       22               12.25               41006.00   
11123                       10                6.75               18912.25   
11124                       44               31.75               10030.75   
11125                       66               44.25               18172.50   

      tuition_los  
0           short  
1           short  
2           short  
3           short  
4           short  
...           ...  
11121       short  
11122       short  
11123       short  
11124       short  
11125       short  

[11126 rows x 10 columns]

In [ ]:
y

0        2 yr Undergrad
1        4 yr Undergrad
2        4 yr Undergrad
3        4 yr Undergrad
4        4 yr Undergrad
              ...      
11121              Grad
11122    5 yr Undergrad
11123    2 yr Undergrad
11124              Grad
11125              Grad
Name: TAP Level of Study, Length: 11126, dtype: object

In [ ]:
x_train, x_test, y_train, y_test = train_test_split(x, y, stratify=y, test_size= 0.25)

In [ ]:
x_test

Academic Year  TAP College Code  Federal School Code  \
477            2019               305                 2734   
25             2020               405                 2758   
6575           2007               650                 2806   
6751           2006              1402                 2694   
6265           2007              5390                 2835   
...             ...               ...                  ...   
6588           2007               575                 2790   
4369           2011               695                 2817   
6318           2007              5030                 2711   
1689           2017              2070                 2866   
8893           2003              2147                 2877   

                       TAP College Name Sector Type TAP Sector Group  \
477                    HOUGHTON COLLEGE     PRIVATE    5-INDEPENDENT   
25     MANHATTAN COLLEGE 4 YR UNDERGRAD     PRIVATE    5-INDEPENDENT   
6575  ROCHESTER INST TECH 4YR UNDERGRAD     PRIVATE    5-INDEPENDENT   
6751               CUNY KINGSBOROUGH CC      PUBLIC        2-CUNY CC   
6265                SUNY AT ALBANY GRAD      PUBLIC        3-SUNY SO   
...                                 ...         ...              ...   
6588        NYACK COLLEGE 4YR UNDERGRAD     PRIVATE    5-INDEPENDENT   
4369       ST BONAVENTURE UNIVERSITY UG     PRIVATE    5-INDEPENDENT   
6318            CORNELL UNIVERSITY GRAD     PRIVATE    5-INDEPENDENT   
1689   FASHION INST TECH-LOWER DIVISION      PUBLIC        4-SUNY CC   
8893         ROCKLAND COMMUNITY COLLEGE      PUBLIC        4-SUNY CC   

      TAP Recipient Headcount  TAP Recipient FTEs  TAP Recipient Dollars  \
477                       341              316.25              885722.00   
25                        817              773.53             2625417.24   
6575                        2                0.67                2080.30   
6751                        2                1.00                1314.00   
6265                      363              281.50               99848.25   
...                       ...                 ...                    ...   
6588                        2                1.00                3499.50   
4369                        5                3.00               14592.00   
6318                       41               34.00               12063.50   
1689                     1140              986.75             2841713.02   
8893                     1049              796.50             1225949.85   

     tuition_los  
477        short  
25         short  
6575       short  
6751       short  
6265       short  
...          ...  
6588       short  
4369       short  
6318       short  
1689       short  
8893       short  

[2782 rows x 10 columns]

In [ ]:
automl = AutoML(results_path="tuition_level", mode="Explain")

In [ ]:
automl.fit(x_train, y_train)

AutoML directory: tuition_level
The task is multiclass_classification with evaluation metric logloss
AutoML will use algorithms: ['Baseline', 'Linear', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 3 models
1_Baseline logloss 1.358953 trained in 0.63 seconds


2_DecisionTree logloss 0.638737 trained in 25.38 seconds
3_Linear logloss 0.737755 trained in 14.49 seconds
* Step default_algorithms will try to check up to 3 models
4_Default_Xgboost logloss 0.175651 trained in 39.61 seconds
5_Default_NeuralNetwork logloss 0.364518 trained in 8.1 seconds
6_Default_RandomForest logloss 0.527478 trained in 17.53 seconds
* Step ensemble will try to check up to 1 model
Ensemble logloss 0.175651 trained in 0.52 seconds
AutoML fit time: 117.35 seconds
AutoML best model: 4_Default_Xgboost


AutoML(results_path='tuition_level')

In [ ]:
pred = automl.predict(x_test)
pred

array(['4 yr Undergrad', '4 yr Undergrad', '2 yr Undergrad', ..., 'Grad',
       '2 yr Undergrad', '2 yr Undergrad'], dtype=object)

In [ ]:
automl.report()

# Regression

In [43]:
df = pd.read_csv("/content/Tuition_Assistance_Program__TAP__Recipients___Dollars_by_College__Sector_Group__and_Level_of_Study__Beginning_2000.csv")
x_cols = [c for c in df.columns if c != "TAP COllege Code"]
x = df[x_cols]
y = df["TAP College Code"]

In [44]:
df

Academic Year  TAP College Code  Federal School Code Level  \
0               2020              1075                 7465     U   
1               2020              8323                42785     U   
2               2020              1040                 2899     U   
3               2020              8244                 7264     U   
4               2020              1016                 2894     U   
...              ...               ...                  ...   ...   
11121           2000              5215                 2688     G   
11122           2000               535                20662     U   
11123           2000               965                 7109     U   
11124           2000              5210                 2681     G   
11125           2000              5205                 2687     G   

      TAP Level of Study                  TAP College Name Sector Type  \
0         2 yr Undergrad    AMERICAN ACAD OF DRAMATIC ARTS     PRIVATE   
1         4 yr Undergrad            YESHIVA HECHAL SHEMUEL     PRIVATE   
2         4 yr Undergrad      WAGNER COLLEGE 4YR UNDERGRAD     PRIVATE   
3         4 yr Undergrad  MESIVTA TORAH VODAATH RABBINICAL     PRIVATE   
4         4 yr Undergrad      UNIV OF ROCHESTER EASTMAN UG     PRIVATE   
...                  ...                               ...         ...   
11121               Grad            CUNY CITY COLLEGE GRAD      PUBLIC   
11122     5 yr Undergrad      THE NEW SCHOOL 4YR UNDERGRAD     PRIVATE   
11123     2 yr Undergrad      SUC OLD WESTBURY (UNDERGRAD)      PUBLIC   
11124               Grad             CANISIUS COLLEGE GRAD     PRIVATE   
11125               Grad        CUNY BROOKLYN COLLEGE GRAD      PUBLIC   

      TAP Sector Group  TAP Recipient Headcount  TAP Recipient FTEs  \
0        5-INDEPENDENT                        3                3.06   
1       9-CHAPTER XXII                        7                7.03   
2        5-INDEPENDENT                      252              239.09   
3       9-CHAPTER XXII                      127              130.41   
4        5-INDEPENDENT                       14               12.73   
...                ...                      ...                 ...   
11121        1-CUNY SR                       56               41.75   
11122    5-INDEPENDENT                       22               12.25   
11123        3-SUNY SO                       10                6.75   
11124    5-INDEPENDENT                       44               31.75   
11125        1-CUNY SR                       66               44.25   

       TAP Recipient Dollars  
0                   12364.30  
1                   25198.17  
2                  722802.93  
3                  551196.83  
4                   30044.02  
...                      ...  
11121               17967.00  
11122               41006.00  
11123               18912.25  
11124               10030.75  
11125               18172.50  

[11126 rows x 11 columns]

In [45]:
x_cols

['Academic Year',
 'TAP College Code',
 'Federal School Code',
 'Level',
 'TAP Level of Study',
 'TAP College Name',
 'Sector Type',
 'TAP Sector Group',
 'TAP Recipient Headcount',
 'TAP Recipient FTEs',
 'TAP Recipient Dollars']

In [46]:
x

Academic Year  TAP College Code  Federal School Code Level  \
0               2020              1075                 7465     U   
1               2020              8323                42785     U   
2               2020              1040                 2899     U   
3               2020              8244                 7264     U   
4               2020              1016                 2894     U   
...              ...               ...                  ...   ...   
11121           2000              5215                 2688     G   
11122           2000               535                20662     U   
11123           2000               965                 7109     U   
11124           2000              5210                 2681     G   
11125           2000              5205                 2687     G   

      TAP Level of Study                  TAP College Name Sector Type  \
0         2 yr Undergrad    AMERICAN ACAD OF DRAMATIC ARTS     PRIVATE   
1         4 yr Undergrad            YESHIVA HECHAL SHEMUEL     PRIVATE   
2         4 yr Undergrad      WAGNER COLLEGE 4YR UNDERGRAD     PRIVATE   
3         4 yr Undergrad  MESIVTA TORAH VODAATH RABBINICAL     PRIVATE   
4         4 yr Undergrad      UNIV OF ROCHESTER EASTMAN UG     PRIVATE   
...                  ...                               ...         ...   
11121               Grad            CUNY CITY COLLEGE GRAD      PUBLIC   
11122     5 yr Undergrad      THE NEW SCHOOL 4YR UNDERGRAD     PRIVATE   
11123     2 yr Undergrad      SUC OLD WESTBURY (UNDERGRAD)      PUBLIC   
11124               Grad             CANISIUS COLLEGE GRAD     PRIVATE   
11125               Grad        CUNY BROOKLYN COLLEGE GRAD      PUBLIC   

      TAP Sector Group  TAP Recipient Headcount  TAP Recipient FTEs  \
0        5-INDEPENDENT                        3                3.06   
1       9-CHAPTER XXII                        7                7.03   
2        5-INDEPENDENT                      252              239.09   
3       9-CHAPTER XXII                      127              130.41   
4        5-INDEPENDENT                       14               12.73   
...                ...                      ...                 ...   
11121        1-CUNY SR                       56               41.75   
11122    5-INDEPENDENT                       22               12.25   
11123        3-SUNY SO                       10                6.75   
11124    5-INDEPENDENT                       44               31.75   
11125        1-CUNY SR                       66               44.25   

       TAP Recipient Dollars  
0                   12364.30  
1                   25198.17  
2                  722802.93  
3                  551196.83  
4                   30044.02  
...                      ...  
11121               17967.00  
11122               41006.00  
11123               18912.25  
11124               10030.75  
11125               18172.50  

[11126 rows x 11 columns]

In [47]:
y

0        1075
1        8323
2        1040
3        8244
4        1016
         ... 
11121    5215
11122     535
11123     965
11124    5210
11125    5205
Name: TAP College Code, Length: 11126, dtype: int64

In [48]:
automl = AutoML()
automl.fit(x, y)

Linear algorithm was disabled.
AutoML directory: AutoML_1
The task is regression with evaluation metric rmse
AutoML will use algorithms: ['Baseline', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 2 models
1_Baseline rmse 2761.685621 trained in 2.52 seconds
2_DecisionTree rmse 199.660753 trained in 12.9 seconds
* Step default_algorithms will try to check up to 3 models
3_Default_Xgboost rmse 3.994924 trained in 12.79 seconds
4_Default_NeuralNetwork rmse 43.200041 trained in 1.92 seconds
5_Default_RandomForest rmse 80.804783 trained in 10.15 seconds
* Step ensemble will try to check up to 1 model
Ensemble rmse 3.994922 trained in 0.31 seconds
AutoML fit time: 49.17 seconds
AutoML best model: 3_Default_Xgboost


AutoML()

In [49]:
df["predictions"] = automl.predict(x)

In [50]:
print("Predictions")
print(df[["TAP College Code", "predictions"]].head())

Predictions
   TAP College Code  predictions
0              1075  1071.956665
1              8323  8323.121094
2              1040  1040.532715
3              8244  8244.034180
4              1016  1016.330750


In [51]:
# get current working directory
import os
os.getcwd()

'/content'

In [59]:
folders = os.listdir()
foldersML = [x for x in folders if x.startswith('AutoML')]
print(foldersML) 

['AutoML_1']


In [60]:
!zip -r /content/AutoML_1.zip /content/AutoML_1

  adding: content/AutoML_1/ (stored 0%)
  adding: content/AutoML_1/data_info.json (deflated 76%)
  adding: content/AutoML_1/ldb_performance_boxplot.png (deflated 21%)
  adding: content/AutoML_1/4_Default_NeuralNetwork/ (stored 0%)
  adding: content/AutoML_1/4_Default_NeuralNetwork/status.txt (stored 0%)
  adding: content/AutoML_1/4_Default_NeuralNetwork/permutation_importance.png (deflated 18%)
  adding: content/AutoML_1/4_Default_NeuralNetwork/learner_fold_0_importance.csv (deflated 37%)
  adding: content/AutoML_1/4_Default_NeuralNetwork/true_vs_predicted.png (deflated 9%)
  adding: content/AutoML_1/4_Default_NeuralNetwork/README.md (deflated 50%)
  adding: content/AutoML_1/4_Default_NeuralNetwork/predicted_vs_residuals.png (deflated 4%)
  adding: content/AutoML_1/4_Default_NeuralNetwork/learner_fold_0.neural_network (stored 0%)
  adding: content/AutoML_1/4_Default_NeuralNetwork/learner_fold_0_training.log (deflated 53%)
  adding: content/AutoML_1/4_Default_NeuralNetwork/framework.jso